In [1]:
!pip install catboost==0.14.2

     |████████████████████████████████| 60.6MB 64kB/s 


In [0]:
from catboost import CatBoostClassifier
from sklearn import model_selection,metrics,preprocessing
from catboost import datasets

In [0]:
train_df,test_df=datasets.amazon()

In [4]:
train_df.shape,test_df.shape

((32769, 10), (58921, 10))

In [5]:
train_df.head()

ACTION  RESOURCE  MGR_ID  ...  ROLE_FAMILY_DESC  ROLE_FAMILY  ROLE_CODE
0       1     39353   85475  ...            117906       290919     117908
1       1     17183    1540  ...            118536       308574     118539
2       1     36724   14457  ...            267952        19721     117880
3       1     36135    5396  ...            240983       290919     118322
4       1     42680    5905  ...            123932        19793     119325

[5 rows x 10 columns]

In [6]:
train_df['ACTION'].value_counts()

1    30872
0     1897
Name: ACTION, dtype: int64

In [7]:
train_df.columns,test_df.columns

(Index(['ACTION', 'RESOURCE', 'MGR_ID', 'ROLE_ROLLUP_1', 'ROLE_ROLLUP_2',
        'ROLE_DEPTNAME', 'ROLE_TITLE', 'ROLE_FAMILY_DESC', 'ROLE_FAMILY',
        'ROLE_CODE'],
       dtype='object'),
 Index(['id', 'RESOURCE', 'MGR_ID', 'ROLE_ROLLUP_1', 'ROLE_ROLLUP_2',
        'ROLE_DEPTNAME', 'ROLE_TITLE', 'ROLE_FAMILY_DESC', 'ROLE_FAMILY',
        'ROLE_CODE'],
       dtype='object'))

In [0]:
x=train_df.drop(['ACTION'],axis=1)
y=train_df['ACTION']
xtest=test_df.drop(['id'],axis=1)

In [0]:
xtr,xval,ytr,yval=model_selection.train_test_split(x,y,test_size=0.25,random_state=42)

In [10]:
params={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'verbose':200,
        'random_seed':42}

clf_1=CatBoostClassifier(**params)
clf_1.fit(xtr,ytr,
          eval_set=(xval,yval),use_best_model=True,plot=True);

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.109208
0:	test: 0.5465232	best: 0.5465232 (0)	total: 137ms	remaining: 2m 17s
200:	test: 0.7924940	best: 0.7926897 (195)	total: 15.4s	remaining: 1m 1s
400:	test: 0.8116729	best: 0.8117242 (399)	total: 29.9s	remaining: 44.7s
600:	test: 0.8199968	best: 0.8200187 (599)	total: 43.1s	remaining: 28.6s
800:	test: 0.8261306	best: 0.8261306 (800)	total: 56.1s	remaining: 13.9s
999:	test: 0.8289469	best: 0.8289469 (999)	total: 1m 8s	remaining: 0us

bestTest = 0.8289468817
bestIteration = 999



tell model about categorical variables

In [13]:
cat_features_names = x.columns # here we specify names of categorical features
cat_features = [x.columns.get_loc(col) for col in cat_features_names]
print(cat_features)

[0, 1, 2, 3, 4, 5, 6, 7, 8]


In [20]:
params_2={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'verbose':200,
        'random_seed':42,
        'cat_features':cat_features}

clf_2=CatBoostClassifier(**params_2)
clf_2.fit(xtr,ytr, eval_set=(xval,yval), use_best_model=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.109208
0:	test: 0.5529024	best: 0.5529024 (0)	total: 180ms	remaining: 2m 59s
200:	test: 0.8821093	best: 0.8826362 (192)	total: 24.8s	remaining: 1m 38s
400:	test: 0.8860194	best: 0.8861194 (388)	total: 50.9s	remaining: 1m 16s
600:	test: 0.8865790	best: 0.8870949 (555)	total: 1m 16s	remaining: 50.6s
800:	test: 0.8867616	best: 0.8874401 (766)	total: 1m 41s	remaining: 25.2s
999:	test: 0.8862418	best: 0.8874401 (766)	total: 2m 6s	remaining: 0us

bestTest = 0.8874401113
bestIteration = 766

Shrink model to first 767 iterations.


In [21]:
params_3={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'verbose':200,
        'random_seed':42,
        'early_stopping_rounds':200,
        'cat_features':cat_features}

clf_3=CatBoostClassifier(**params_3)
clf_3.fit(xtr,ytr, eval_set=(xval,yval), use_best_model=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.109208
0:	test: 0.5529024	best: 0.5529024 (0)	total: 162ms	remaining: 2m 41s
200:	test: 0.8821093	best: 0.8826362 (192)	total: 24.6s	remaining: 1m 37s
400:	test: 0.8860194	best: 0.8861194 (388)	total: 50.6s	remaining: 1m 15s
600:	test: 0.8865790	best: 0.8870949 (555)	total: 1m 15s	remaining: 50.3s
800:	test: 0.8867616	best: 0.8874401 (766)	total: 1m 41s	remaining: 25.2s
Stopped by overfitting detector  (200 iterations wait)

bestTest = 0.8874401113
bestIteration = 766

Shrink model to first 767 iterations.


In [24]:
#add noise features
import numpy as np
np.random.seed(42)
noise_cols = [f'noise_{i}' for i in range(5)]
for col in noise_cols:
    xtr[col] = ytr * np.random.rand(xtr.shape[0])
    xval[col] = np.random.rand(xval.shape[0])

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [25]:
params_3={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'verbose':200,
        'random_seed':42,
        'early_stopping_rounds':200,
        'cat_features':cat_features}

clf_3=CatBoostClassifier(**params_3)
clf_3.fit(xtr,ytr, eval_set=(xval,yval), use_best_model=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.109208
0:	test: 0.5009180	best: 0.5009180 (0)	total: 154ms	remaining: 2m 33s
200:	test: 0.5073142	best: 0.5078097 (49)	total: 19.8s	remaining: 1m 18s
Stopped by overfitting detector  (200 iterations wait)

bestTest = 0.5078096791
bestIteration = 49

Shrink model to first 50 iterations.


In [27]:
clf_3.get_feature_importance(prettified=True)

[('noise_2', 43.25109551431068),
 ('noise_3', 21.215804518467543),
 ('noise_0', 15.475190881645853),
 ('noise_1', 11.38724885770959),
 ('noise_4', 7.554669028212862),
 ('ROLE_ROLLUP_1', 0.9978284327923403),
 ('ROLE_FAMILY', 0.11816276686112372),
 ('RESOURCE', 0.0),
 ('MGR_ID', 0.0),
 ('ROLE_ROLLUP_2', 0.0),
 ('ROLE_DEPTNAME', 0.0),
 ('ROLE_TITLE', 0.0),
 ('ROLE_FAMILY_DESC', 0.0),
 ('ROLE_CODE', 0.0)]

In [28]:
ignored_features = list(range(xtr.shape[1] - 5, xtr.shape[1]))
print(ignored_features)

[9, 10, 11, 12, 13]


In [17]:
params_3={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'verbose':200,
        'random_seed':42,
        'early_stopping_rounds':200,
        'cat_features':cat_features}
        #'ignored_features':ignored_features}

clf_3=CatBoostClassifier(**params_3)
clf_3.fit(xtr,ytr, eval_set=(xval,yval), use_best_model=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.109208
0:	test: 0.5529024	best: 0.5529024 (0)	total: 183ms	remaining: 3m 2s
200:	test: 0.8821093	best: 0.8826362 (192)	total: 24.2s	remaining: 1m 36s
400:	test: 0.8860194	best: 0.8861194 (388)	total: 49.8s	remaining: 1m 14s
600:	test: 0.8865790	best: 0.8870949 (555)	total: 1m 14s	remaining: 49.5s
800:	test: 0.8867616	best: 0.8874401 (766)	total: 1m 39s	remaining: 24.6s
Stopped by overfitting detector  (200 iterations wait)

bestTest = 0.8874401113
bestIteration = 766

Shrink model to first 767 iterations.


In [0]:
from catboost import Pool

In [0]:
train_set=Pool(data=xtr,label=ytr,cat_features=cat_features)
valid_set=Pool(data=xval,label=yval,cat_features=cat_features)

In [33]:
params={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'ignored_features':ignored_features,
        'early_stopping_rounds':200,
        'n_estimators':2000,
        'verbose':200,
        'random_seed':4}

clf_7=CatBoostClassifier(**params)
clf_7.fit(train_set,eval_set=valid_set,use_best_model=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.081173
0:	test: 0.5007413	best: 0.5007413 (0)	total: 138ms	remaining: 4m 34s
200:	test: 0.8857790	best: 0.8859278 (191)	total: 23.8s	remaining: 3m 32s
400:	test: 0.8889166	best: 0.8890010 (397)	total: 50.5s	remaining: 3m 21s
600:	test: 0.8892811	best: 0.8893263 (579)	total: 1m 16s	remaining: 2m 58s
800:	test: 0.8895345	best: 0.8897523 (633)	total: 1m 42s	remaining: 2m 33s
Stopped by overfitting detector  (200 iterations wait)

bestTest = 0.8897522909
bestIteration = 633

Shrink model to first 634 iterations.


Cross validation in Catboost

In [0]:
from catboost import cv

In [21]:
params={'loss_function':'Logloss',
        'eval_metric':'AUC',
        'random_seed':7,
        'verbose':200}
all_data=Pool(data=x,label=y,cat_features=cat_features)

scores=cv(pool=all_data,params=params,fold_count=5,
          seed=78,stratified=True,shuffle=True,plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	test: 0.5716710	best: 0.5716710 (0)
200:	test: 0.8840841	best: 0.8840841 (200)
400:	test: 0.8888771	best: 0.8888802 (399)
600:	test: 0.8901704	best: 0.8901704 (600)
800:	test: 0.8911647	best: 0.8911709 (799)
999:	test: 0.8917486	best: 0.8917765 (983)	total: 14m 45s	remaining: 0us


iterations  test-AUC-mean  ...  train-Logloss-mean  train-Logloss-std
0             0       0.571671  ...            0.641950           0.000730
1             1       0.591038  ...            0.596071           0.001121
2             2       0.591433  ...            0.555551           0.000960
3             3       0.601432  ...            0.519300           0.001406
4             4       0.621867  ...            0.486577           0.001903
..          ...            ...  ...                 ...                ...
995         995       0.891758  ...            0.143927           0.000633
996         996       0.891758  ...            0.143924           0.000633
997         997       0.891751  ...            0.143916           0.000637
998         998       0.891752  ...            0.143914           0.000639
999         999       0.891749  ...            0.143905           0.000634

[1000 rows x 7 columns]